# Zadanie 3

Na podstawie bazy danych (`szczecin.gpkg`) i wykorzystując geopandas:

- wyznacż losowo 10 przystanków komunikacji miejskiej
- wykonaj bufor wokół przystanku o średnicy 500 m
- oblicz całkowitą powierzchnię mieszkalną oraz w poszuczególnych klasach budynków zabudowy
- wyznacz 3 przystanki o największej powierzchni mieszkalne
- dane wywietl w tabeli oraz na mapie

In [1]:
import geopandas as gpd
import matplotlib.pyplot as plt
import geoplot
import pandas as pd
import json
import folium

In [2]:
filename = 'szczecin.gpkg'
szczecin_gdf = gpd.read_file(filename, layer="OT_OIKM_P")
mieszkania_gdf = gpd.read_file(filename, layer="OT_BUBD_A")

## Wyzanczenie losowych przystanków komunikacji

In [3]:
bus_stops = szczecin_gdf[szczecin_gdf["x_kod"] == "OIKM04"]
random_bus_stops = bus_stops.sample(10)

## Bufor w okół przystanków

In [4]:
bufor = random_bus_stops.buffer(500, resolution=16)
bufor_gdf = gpd.GeoDataFrame()
bufor_gdf.insert(0, 'nazwaPrzystanku', random_bus_stops.nazwa)
bufor_gdf.insert(1, 'geometry', bufor)
bufor_gdf = bufor_gdf.to_crs("EPSG:2180")

# Obliczanie powierzchni

In [5]:
intersected = gpd.overlay(mieszkania_gdf, bufor_gdf, how='intersection')
intersected = intersected[(
    (intersected["x_kod"] == "BUBD01") |
    (intersected["x_kod"] == "BUBD02") |
    (intersected["x_kod"] == "BUBD03") |
    (intersected["x_kod"] == "BUBD04"))]
area = intersected.area


s = area * intersected.liczbakond
s = s.sum()

In [6]:
print("Łączna powierzchnia mieszkalna =", s)

Łączna powierzchnia mieszkalna = 9122657.187400263


In [7]:
names = intersected.nazwaPrzystanku
data = {
    "Powierzchnia": area * intersected.liczbakond,
    "Przystanek": names
    }
area_df = pd.DataFrame(data)
area_df.groupby(["Przystanek"]).sum().sort_values(by=["Powierzchnia"], ascending=False)

Powierzchnia
Przystanek                          
Unii Lubelskiej         7.125554e+06
WĹ‚adysĹ‚awa Ĺokietka  1.067156e+06
UrzÄ…d Miejski          4.176890e+05
SmolaĹ„ska              1.403203e+05
Hutnicza                1.268452e+05
Jana z Czarnolasu       1.216483e+05
Rozmarynowa             1.093530e+05
ĹukasiĹ„skiego Ogrody  1.361319e+04
Basen GĂłrniczy         4.782024e+02

## Wizualizacja

In [8]:
m = folium.Map(
    location=[53.4327,14.5483],
    tiles='OpenStreetMap',
    zoom_start=12,
    control_scale=True,
    crs='EPSG3857'
)

folium.GeoJson(intersected).add_to(m)
folium.GeoJson(bufor).add_to(m)

m